In [2]:
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.model_selection import KFold
from sklearn.ensemble import RandomForestClassifier
from sklearn.cross_validation import cross_val_score
import numpy as np
from sklearn.metrics import confusion_matrix
from sklearn.decomposition import PCA as sklearnPCA
from sklearn.preprocessing import StandardScaler
import sys
import os
import pickle
%matplotlib inline

### Here we are building the model using only the quant.sf file.

In [3]:
df = pd.read_csv("project1/train/ERR188021/bias/quant.sf",low_memory=False,sep='\t')

In [4]:
df.head(10)

Name  Length  EffectiveLength       TPM   NumReads
0  ENST00000456328.2    1657          1412.34  0.221792    7.10108
1  ENST00000450305.2     632           174.00  0.000000    0.00000
2  ENST00000488147.1    1351          1364.77  5.420600  167.70400
3  ENST00000619216.1      68            20.00  0.000000    0.00000
4  ENST00000473358.1     712           174.00  0.000000    0.00000
5  ENST00000469289.1     535           174.00  0.000000    0.00000
6  ENST00000607096.1     138            16.00  0.000000    0.00000
7  ENST00000417324.1    1187           944.77  0.000000    0.00000
8  ENST00000461467.1     590           383.91  1.080040    9.39954
9  ENST00000606857.1     840           174.00  0.000000    0.00000

In [5]:
df.shape

(199324, 5)

In [6]:
df.sort_values('TPM',ascending = False).head(10)

Name  Length  EffectiveLength      TPM  NumReads
199305  ENST00000361739.1     684          459.340  14493.4  150918.0
199302  ENST00000361624.2    1542         1155.690  13877.0  363559.0
199309  ENST00000362079.2     784          526.212  13537.0  161482.0
70171   ENST00000331789.9    1917         1914.490  13520.6  586798.0
192647  ENST00000451311.6     628          500.270  12547.0  142293.0
199308  ENST00000361899.2     681          392.210  12196.6  108442.0
199307  ENST00000361851.1     207           53.000  11293.8   13569.2
185574  ENST00000627981.1     923          894.379  10094.2  204659.0
185561  ENST00000631211.1     923          894.379  10094.2  204659.0
185570  ENST00000625598.1     923          894.379  10094.1  204658.0

In [7]:
df = df.filter(['Name','TPM'])

### 980 transcripts have more than 100 TPM count in 1 person. 

In [8]:
df = df[df['TPM'] >= 100]
df.shape

(980, 2)

In [9]:
dfT = df.set_index("Name")
dfT = dfT.T

In [10]:
transcriptList = dfT.columns

In [11]:
dfT.columns

Index(['ENST00000457540.1', 'ENST00000514057.1', 'ENST00000379389.4',
       'ENST00000344843.11', 'ENST00000378609.8', 'ENST00000234875.8',
       'ENST00000471204.5', 'ENST00000493373.5', 'ENST00000338639.9',
       'ENST00000234590.8',
       ...
       'ENST00000361899.2', 'ENST00000362079.2', 'ENST00000361227.2',
       'ENST00000361335.1', 'ENST00000361381.2', 'ENST00000361567.2',
       'ENST00000361681.2', 'ENST00000387459.1', 'ENST00000361789.2',
       'ENST00000387461.2'],
      dtype='object', name='Name', length=980)

In [12]:
transcriptDict = dict()
for i in range(len(transcriptList)):
    if transcriptDict.__contains__(transcriptList[i]):
        transcriptDict[transcriptList[i]] = transcriptDict.get(transcriptList[i]) + 1
    else:
        transcriptDict[transcriptList[i]] = 1

In [7]:
traincsv = pd.read_csv("project1/p1_train.csv",low_memory=False)

In [8]:
traincsv.head(10)

accession label
0  ERR188441   CEU
1  ERR188180   FIN
2  ERR188420   CEU
3  ERR188032   CEU
4  ERR188296   FIN
5  ERR188401   GBR
6  ERR188254   TSI
7  ERR188391   GBR
8  ERR188117   FIN
9  ERR188133   GBR

In [9]:
traincsv['label'].value_counts()

FIN    77
GBR    77
TSI    72
CEU    72
YRI    71
Name: label, dtype: int64

In [10]:
accessionList = traincsv['accession'].values
countryList = traincsv['label'].values

In [11]:
transcriptDict = dict()

### This is the code to read quant.sf files for each person and here we are making superset of of all the transcripts having less than 100 TPM in any of the person.

In [12]:
globaldf = pd.DataFrame()
def readAllQuantSFFiles():
    for i in range(len(accessionList)):
        name = accessionList[i]
        df = pd.read_csv("project1/train/"+ str(name) + "/bias/quant.sf",low_memory=False,sep='\t')
        extractTopTranscripts(df)

In [13]:
def extractTopTranscripts(df):
    df = df.filter(['Name','TPM'])
    df = df[df['TPM'] <= 100]
    dfT = df.set_index("Name")
    dfT = dfT.T
    transcriptList = dfT.columns
    buildTranscriptDict(transcriptList)

In [14]:
def buildTranscriptDict(transcriptList):
    for i in range(len(transcriptList)):
        global transcriptDict
        if transcriptDict.__contains__(transcriptList[i]):
            transcriptDict[transcriptList[i]] = transcriptDict.get(transcriptList[i]) + 1
        else:
            transcriptDict[transcriptList[i]] = 1

In [15]:
readAllQuantSFFiles()

In [16]:
print(len(transcriptDict))

199022


In [17]:
for key in transcriptDict.keys():
    print(key,transcriptDict.get(key))

ENST00000456328.2 369
ENST00000450305.2 369
ENST00000488147.1 369
ENST00000619216.1 369
ENST00000473358.1 369
ENST00000469289.1 369
ENST00000607096.1 369
ENST00000417324.1 369
ENST00000461467.1 369
ENST00000606857.1 369
ENST00000492842.1 369
ENST00000335137.3 369
ENST00000466430.5 369
ENST00000477740.5 369
ENST00000471248.1 369
ENST00000610542.1 369
ENST00000453576.2 369
ENST00000495576.1 369
ENST00000442987.3 369
ENST00000494149.2 369
ENST00000595919.1 369
ENST00000493797.1 369
ENST00000484859.1 369
ENST00000490997.5 369
ENST00000466557.6 369
ENST00000491962.1 369
ENST00000410691.1 369
ENST00000496488.1 369
ENST00000624431.2 369
ENST00000623083.4 369
ENST00000612080.1 369
ENST00000442116.1 369
ENST00000448958.1 369
ENST00000634344.1 369
ENST00000424587.6 369
ENST00000335577.4 369
ENST00000450734.1 369
ENST00000458203.2 369
ENST00000441866.1 369
ENST00000450983.1 369
ENST00000412666.1 369
ENST00000635159.1 369
ENST00000431321.1 369
ENST00000453935.1 369
ENST00000440163.1 369
ENST000004

ENST00000467612.5 369
ENST00000610898.1 369
ENST00000496707.5 369
ENST00000463043.1 369
ENST00000377648.4 369
ENST00000495385.1 369
ENST00000054650.8 369
ENST00000484676.1 369
ENST00000307896.10 369
ENST00000377627.7 369
ENST00000484669.6 369
ENST00000487819.5 369
ENST00000472925.1 369
ENST00000480647.1 369
ENST00000465508.5 369
ENST00000451196.5 369
ENST00000377577.9 369
ENST00000294401.11 369
ENST00000472414.1 369
ENST00000426784.1 369
ENST00000473993.5 369
ENST00000469318.5 369
ENST00000485073.5 369
ENST00000460594.5 369
ENST00000465911.1 369
ENST00000432429.5 369
ENST00000414210.5 369
ENST00000635029.1 369
ENST00000635092.1 369
ENST00000421469.2 369
ENST00000442889.1 369
ENST00000303635.11 369
ENST00000490738.5 369
ENST00000476163.5 369
ENST00000473578.5 369
ENST00000557126.5 369
ENST00000467404.6 369
ENST00000461311.1 369
ENST00000486138.1 369
ENST00000482934.1 369
ENST00000470648.5 369
ENST00000461580.5 369
ENST00000472283.1 369
ENST00000467267.1 369
ENST00000495233.5 369
ENST000

ENST00000618240.4 369
ENST00000465372.5 369
ENST00000492982.6 369
ENST00000437606.6 369
ENST00000484418.1 369
ENST00000475814.5 369
ENST00000530874.1 369
ENST00000478858.5 369
ENST00000608765.1 369
ENST00000449467.2 369
ENST00000361729.2 369
ENST00000487237.1 369
ENST00000451217.1 369
ENST00000374561.5 367
ENST00000463312.1 369
ENST00000486541.1 369
ENST00000477916.5 369
ENST00000374555.7 369
ENST00000612756.1 369
ENST00000451300.2 369
ENST00000467075.1 369
ENST00000482370.1 369
ENST00000443624.5 369
ENST00000458455.1 369
ENST00000418390.6 369
ENST00000613537.4 369
ENST00000609199.1 369
ENST00000487554.1 369
ENST00000427796.5 369
ENST00000447961.1 369
ENST00000246151.8 369
ENST00000415372.1 369
ENST00000374524.1 369
ENST00000374514.7 369
ENST00000420982.5 369
ENST00000374505.6 369
ENST00000495365.5 369
ENST00000374503.7 369
ENST00000374502.7 369
ENST00000492577.1 369
ENST00000421070.1 369
ENST00000374501.1 369
ENST00000472213.1 369
ENST00000481736.5 369
ENST00000617979.4 369
ENST000003

ENST00000466743.1 369
ENST00000447495.1 369
ENST00000453908.7 369
ENST00000505871.6 369
ENST00000480549.5 369
ENST00000496636.1 369
ENST00000508854.1 369
ENST00000474766.1 369
ENST00000270824.1 369
ENST00000490466.1 369
ENST00000373137.2 369
ENST00000359297.6 369
ENST00000373129.7 369
ENST00000373130.7 369
ENST00000373132.3 369
ENST00000460417.5 369
ENST00000473733.5 369
ENST00000482458.1 369
ENST00000460017.1 369
ENST00000476041.1 369
ENST00000315732.2 369
ENST00000489912.1 369
ENST00000410889.1 369
ENST00000468441.5 369
ENST00000495222.5 369
ENST00000235532.9 369
ENST00000356637.9 369
ENST00000471369.1 369
ENST00000433045.6 369
ENST00000445843.7 369
ENST00000475160.1 369
ENST00000525869.1 369
ENST00000528112.1 369
ENST00000354267.3 369
ENST00000524789.1 369
ENST00000364578.1 369
ENST00000373116.5 269
ENST00000488606.5 369
ENST00000477040.1 369
ENST00000462067.1 369
ENST00000373103.5 369
ENST00000373106.5 369
ENST00000373104.5 369
ENST00000480825.6 369
ENST00000361632.8 369
ENST000004

ENST00000372168.7 369
ENST00000372172.4 369
ENST00000486296.5 369
ENST00000466423.5 369
ENST00000487488.5 369
ENST00000484564.1 369
ENST00000246337.8 369
ENST00000491773.5 369
ENST00000463092.5 369
ENST00000636293.1 369
ENST00000636836.1 369
ENST00000461035.5 369
ENST00000491300.5 369
ENST00000434478.5 369
ENST00000494399.5 369
ENST00000460334.5 369
ENST00000462688.5 369
ENST00000460906.5 369
ENST00000490385.5 369
ENST00000469548.5 369
ENST00000486699.5 369
ENST00000478467.5 369
ENST00000428106.1 369
ENST00000496439.1 369
ENST00000473012.1 369
ENST00000472254.1 369
ENST00000466193.1 369
ENST00000465678.1 369
ENST00000359600.5 369
ENST00000464588.1 369
ENST00000425293.1 369
ENST00000626198.1 369
ENST00000334815.4 369
ENST00000529984.5 369
ENST00000485271.5 369
ENST00000372104.5 369
ENST00000448481.5 369
ENST00000456914.6 369
ENST00000354383.10 369
ENST00000475516.5 369
ENST00000355498.6 369
ENST00000372098.7 369
ENST00000481571.5 369
ENST00000372110.7 369
ENST00000372115.7 369
ENST00000

...

ENST00000473806.5 369
ENST00000483645.5 369
ENST00000494268.1 369
ENST00000380691.2 369
ENST00000467141.1 369
ENST00000473380.1 369
ENST00000384065.1 369
ENST00000380682.5 369
ENST00000616992.1 369
ENST00000640291.1 369
ENST00000384068.1 369
ENST00000425057.1 369
ENST00000443728.1 369
ENST00000619728.1 369
ENST00000606842.1 369
ENST00000380663.7 369
ENST00000380668.9 369
ENST00000398491.6 369
ENST00000489404.5 369
ENST00000461630.1 369
ENST00000457574.1 369
ENST00000453682.1 369
ENST00000380659.3 369
ENST00000484204.1 369
ENST00000451564.1 369
ENST00000218032.6 369
ENST00000311912.5 369
ENST00000380635.5 369
ENST00000380633.1 369
ENST00000542843.5 369
ENST00000380625.7 369
ENST00000468287.1 369
ENST00000333995.7 369
ENST00000438997.1 369
ENST00000568788.1 369
ENST00000412485.1 369
ENST00000443965.1 369
ENST00000431486.1 369
ENST00000380622.4 369
ENST00000622204.1 369
ENST00000458400.1 369
ENST00000419566.5 369
ENST00000456091.1 369
ENST00000446964.1 369
ENST00000420403.1 369
ENST000003

ENST00000455775.6 369
ENST00000557224.5 369
ENST00000518685.5 369
ENST00000376197.1 369
ENST00000466508.5 369
ENST00000055335.10 369
ENST00000495799.5 369
ENST00000471261.2 369
ENST00000376188.1 369
ENST00000602455.1 369
ENST00000407599.3 369
ENST00000442437.2 369
ENST00000612958.1 369
ENST00000621907.1 369
ENST00000361446.5 369
ENST00000420398.2 369
ENST00000405679.3 369
ENST00000639028.1 369
ENST00000440137.1 369
ENST00000381698.3 369
ENST00000445148.1 369
ENST00000381722.1 369
ENST00000610680.4 369
ENST00000381709.6 369
ENST00000381700.10 369
ENST00000619375.1 369
ENST00000362097.1 369
ENST00000423609.1 369
ENST00000438101.1 369
ENST00000376150.3 369
ENST00000376141.5 369
ENST00000218068.6 369
ENST00000478785.1 369
ENST00000474146.1 369
ENST00000437322.2 369
ENST00000621775.1 369
ENST00000402231.1 369
ENST00000376088.7 369
ENST00000376091.7 369
ENST00000482218.2 369
ENST00000376108.7 369
ENST00000307367.2 369
ENST00000364471.1 369
ENST00000385025.1 369
ENST00000385034.3 369
ENST0000

ENST00000468904.1 369
ENST00000332270.6 369
ENST00000450457.6 369
ENST00000450049.6 369
ENST00000372953.8 369
ENST00000494863.2 369
ENST00000545398.5 369
ENST00000372939.5 369
ENST00000372935.5 369
ENST00000372936.3 369
ENST00000478422.1 369
ENST00000488615.1 369
ENST00000443801.2 369
ENST00000372930.4 369
ENST00000478351.1 369
ENST00000403304.6 369
ENST00000435570.1 369
ENST00000372926.5 369
ENST00000372927.5 369
ENST00000423383.2 369
ENST00000490943.2 369
ENST00000402866.5 369
ENST00000395209.7 369
ENST00000541709.5 369
ENST00000372916.8 369
ENST00000538510.1 369
ENST00000372907.7 369
ENST00000324762.10 369
ENST00000356784.1 369
ENST00000365154.1 369
ENST00000603059.2 369
ENST00000331267.5 369
ENST00000372902.3 369
ENST00000480575.1 369
ENST00000618050.4 369
ENST00000372880.5 369
ENST00000621635.4 369
ENST00000308731.7 369
ENST00000470069.1 369
ENST00000488970.1 369
ENST00000478995.1 369
ENST00000470329.1 369
ENST00000464006.1 369
ENST00000464567.1 369
ENST00000427805.6 369
ENST00000

ENST00000618570.1 369
ENST00000436312.2 369
ENST00000441721.1 369
ENST00000457130.2 369
ENST00000365042.1 369
ENST00000448560.1 369
ENST00000414071.1 369
ENST00000370493.3 369
ENST00000443260.1 369
ENST00000603091.1 369
ENST00000625029.1 369
ENST00000335565.4 369
ENST00000370490.1 369
ENST00000408967.2 369
ENST00000516410.2 369
ENST00000401256.1 369
ENST00000401186.1 369
ENST00000401124.1 369
ENST00000401279.1 369
ENST00000401245.1 369
ENST00000401237.1 369
ENST00000364724.1 369
ENST00000421173.1 369
ENST00000446870.1 369
ENST00000445173.1 369
ENST00000438525.2 369
ENST00000458472.1 369
ENST00000421282.1 369
ENST00000603634.1 369
ENST00000639829.1 369
ENST00000401352.1 369
ENST00000385136.2 369
ENST00000385138.1 369
ENST00000385249.1 369
ENST00000384998.1 369
ENST00000385234.1 369
ENST00000384857.1 369
ENST00000516774.2 369
ENST00000390724.1 369
ENST00000390725.1 369
ENST00000385265.1 369
ENST00000384909.1 369
ENST00000385133.1 369
ENST00000385131.1 369
ENST00000385132.1 369
ENST000006

ENST00000432335.1 369
ENST00000344884.4 369
ENST00000491902.1 369
ENST00000382852.1 369
ENST00000304790.3 369
ENST00000505047.1 369
ENST00000432046.1 369
ENST00000504503.1 369
ENST00000428070.1 369
ENST00000514804.1 369
ENST00000432915.1 369
ENST00000454868.1 369
ENST00000435142.1 369
ENST00000516161.1 369
ENST00000454643.1 369
ENST00000407745.1 369
ENST00000324446.3 369
ENST00000454875.1 369
ENST00000452584.5 369
ENST00000331787.2 369
ENST00000447937.1 369
ENST00000610801.1 369
ENST00000403487.2 369
ENST00000382840.3 369
ENST00000516957.1 369
ENST00000615809.1 369
ENST00000431768.2 369
ENST00000441139.5 369
ENST00000400605.5 369
ENST00000513194.1 369
ENST00000407724.7 369
ENST00000459719.6 369
ENST00000447520.5 369
ENST00000445715.5 369
ENST00000538014.2 369
ENST00000447202.2 369
ENST00000588613.5 369
ENST00000589075.5 369
ENST00000585549.5 369
ENST00000587095.1 369
ENST00000488280.1 369
ENST00000253320.8 369
ENST00000593000.1 369
ENST00000592697.1 369
ENST00000586015.1 369
ENST000005

In [18]:
globaldf = pd.DataFrame()

In [19]:
def makeGlobalDF():
    for i in range(len(accessionList)):
        name = accessionList[i]
        df = pd.read_csv("project1/train/"+ str(name) + "/bias/quant.sf",low_memory=False,sep='\t')
        addPersonCountry(df,i)     

In [20]:
def addPersonCountry(df,index):
    df = df.filter(['Name','TPM'])
    dfT = df.set_index("Name")
    dfT = dfT.T
    dfT = dfT.filter(transcriptDict.keys())
    dfT['PersonID'] = accessionList[index]
    dfT['Country'] = countryList[index]
    global globaldf
    globaldf = globaldf.append(dfT)

In [21]:
makeGlobalDF()

In [22]:
globaldf.shape

(369, 199024)

In [23]:
globaldf.head(10)

Name  ENST00000456328.2  ENST00000450305.2  ENST00000488147.1  \
TPM            0.014166                0.0            3.10743   
TPM            0.050676                0.0            5.69637   
TPM            0.181035                0.0            2.26863   
TPM            0.000000                0.0            4.41379   
TPM            0.000000                0.0            2.59099   
TPM            0.000000                0.0            7.63196   
TPM            0.258589                0.0            3.37701   
TPM            0.333180                0.0            4.44307   
TPM            0.242421                0.0            5.40468   
TPM            0.264581                0.0            4.14539   

Name  ENST00000619216.1  ENST00000473358.1  ENST00000469289.1  \
TPM             1.06015           0.000000                0.0   
TPM             0.00000           0.000000                0.0   
TPM             0.00000           0.000000                0.0   
TPM             0.00000           0.001128                0.0   
TPM             0.00000           0.000000                0.0   
TPM             0.00000           0.000000                0.0   
TPM             0.00000           0.000000                0.0   
TPM             0.00000           0.000000                0.0   
TPM             0.00000           0.000000                0.0   
TPM             0.00000           0.000000                0.0   

Name  ENST00000607096.1  ENST00000417324.1  ENST00000461467.1  \
TPM            0.000000                0.0           0.655344   
TPM            0.000000                0.0           0.657210   
TPM            0.229779                0.0           0.965807   
TPM            0.936256                0.0           0.686672   
TPM            0.000000                0.0           0.732263   
TPM            0.000000                0.0           0.588230   
TPM            0.000000                0.0           0.623555   
TPM            0.000000                0.0           0.356349   
TPM            0.000000                0.0           0.121667   
TPM            0.000000                0.0           2.312060   

Name  ENST00000606857.1   ...     ENST00000318388.10  ENST00000245903.3  \
TPM                 0.0   ...                177.678            340.316   
TPM                 0.0   ...                201.565            294.315   
TPM                 0.0   ...                146.381            176.654   
TPM                 0.0   ...                165.841            291.636   
TPM                 0.0   ...                164.553            270.261   
TPM                 0.0   ...                199.052            325.277   
TPM                 0.0   ...                158.781            282.474   
TPM                 0.0   ...                167.560            278.294   
TPM                 0.0   ...                166.960            287.051   
TPM                 0.0   ...                157.772            224.946   

Name  ENST00000291295.13  ENST00000246802.9  ENST00000391851.8  \
TPM              297.008            207.994            183.409   
TPM              201.073            267.382            180.977   
TPM              211.970            228.793            206.973   
TPM              232.277            282.092            171.827   
TPM              261.543            188.913            198.825   
TPM              239.086            190.547            268.544   
TPM              189.554            265.037            254.997   
TPM              182.823            284.541            222.206   
TPM              179.657            228.730            201.483   
TPM              206.015            154.696            183.655   

Name  ENST00000400137.8  ENST00000284971.7  ENST00000270142.10   PersonID  \
TPM             209.365            211.758             233.884  ERR188441   
TPM             225.262            182.337             217.617  ERR188180   
TPM             166.585            197.847             215.670  ERR1

In [ ]:
globaldf.to_csv("Global.csv",index=False)

In [435]:
rf_model = RandomForestClassifier(n_estimators=500, # Number of trees
                                  max_features=1000,    # Num features considered
                                  oob_score=True)    # Use OOB scoring*
trainList = globaldf.columns
trainList = trainList[0:-3]

features = trainList
traindf = globaldf.head(300)
# Train the model
rf_model.fit(X=traindf[features],
             y=traindf["Country"])

print("OOB accuracy: ")
print(rf_model.oob_score_)

OOB accuracy: 
0.813333333333


In [436]:
testDF = globaldf.iloc[300:400]
predictedDF = rf_model.predict(testDF[features])

In [437]:
predictedDF

array(['FIN', 'TSI', 'FIN', 'TSI', 'TSI', 'YRI', 'FIN', 'TSI', 'CEU',
       'YRI', 'TSI', 'GBR', 'FIN', 'YRI', 'YRI', 'YRI', 'GBR', 'YRI',
       'FIN', 'GBR', 'CEU', 'TSI', 'FIN', 'CEU', 'CEU', 'CEU', 'FIN',
       'GBR', 'GBR', 'TSI', 'GBR', 'FIN', 'YRI', 'CEU', 'FIN', 'YRI',
       'GBR', 'YRI', 'CEU', 'TSI', 'YRI', 'CEU', 'CEU', 'TSI', 'CEU',
       'GBR', 'FIN', 'FIN', 'CEU', 'FIN', 'CEU', 'FIN', 'GBR', 'CEU',
       'GBR', 'FIN', 'YRI', 'TSI', 'TSI', 'FIN', 'YRI', 'FIN', 'GBR',
       'TSI', 'GBR', 'YRI', 'TSI', 'CEU', 'CEU'], dtype=object)

In [438]:
ansList = testDF['Country'].tolist()

In [439]:
checkDict = dict()
for i in range(len(ansList)):
        global checkDict
        if checkDict.__contains__(ansList[i]):
            checkDict[ansList[i]] = checkDict.get(ansList[i]) + 1
        else:
            checkDict[ansList[i]] = 1

In [440]:
print(checkDict)

{'TSI': 11, 'GBR': 19, 'YRI': 12, 'FIN': 17, 'CEU': 10}


In [441]:
count = 0
for i in range(len(ansList)):
    if ansList[i] == predictedDF[i]:
        count += 1
print(count/len(ansList))

0.782608695652174


In [32]:
confusion_matrix(ansList,predictedDF,labels=['GBR', 'FIN', 'CEU', 'TSI', 'YRI'])

array([[16,  1,  0,  1,  0],
       [ 0, 12,  0,  1,  0],
       [ 0,  2, 17,  1,  0],
       [ 2,  1,  1, 19,  0],
       [ 0,  0,  0,  0, 21]])

In [443]:
maskdf = pd.read_csv("Global.csv")

In [28]:
maskdf = globaldf

In [29]:
maskdf.shape

(369, 199024)

### Here we are training our model on transcripts having less than 100 TPM and we are getting 89.5 % accuracy.

In [31]:
cross_val = 1
averageAccuracyScore = 0
rf_model = RandomForestClassifier(n_estimators=300, # Number of trees
                                    max_features=199000,    # Num features considered
                                    oob_score=False)    # Use OOB scoring*
for i in range(cross_val):
    msk = np.random.rand(len(maskdf)) < 0.80

    train = maskdf[msk]
    
    test = maskdf[~msk]


    trainList = maskdf.columns
    trainList = trainList[0:-3]

    features = trainList
    
#     XTrain_std = StandardScaler().fit_transform(train.filter(trainList))
#     XTest_std = StandardScaler().fit_transform(test.filter(trainList))

    # Train the model
    rf_model.fit(X=train[features],
                 y=train["Country"])
    
#     print("OOB accuracy: ")
#     print(rf_model.oob_score_)

    predictedDF = rf_model.predict(test[features])
    ansList = test['Country'].tolist()
    global averageAccuracyScore
    averageAccuracyScore += printAccuracy(ansList,predictedDF)
print("Average Accuracy of model is " + str(averageAccuracyScore/cross_val))

Average Accuracy of model is 0.8947368421052632


In [26]:
def printAccuracy(ansList,predictedDF):
    count = 0
    for i in range(len(ansList)):
        if ansList[i] == predictedDF[i]:
            count += 1
#     print(count/len(ansList))
    return (count/len(ansList))

In [72]:
def permutationTest():
    trainList = maskdf.columns
    trainList = trainList[0:-3]
    features = trainList
    predictedDF = rf_model.predict(maskdf[features])
    ansList = maskdf['Country'].tolist()
    permutationList = list()
    for i in range(500):
        dfshuffle = np.random.permutation(maskdf.Country)
        permutationList.append(printAccuracy(dfshuffle,predictedDF))
    print("Average Accuracy of permutation Test is :",sum(permutationList)/500)

### We have performed Permutation Test to check that our model is just not guessing the classes. The accuracy obtained on P test is just 20 % which shows our model is performing well.

In [73]:
permutationTest()

Average Accuracy of permutation Test is : 0.20121951219512213


In [243]:
colList = globaldf.columns
colListWithoutCoun = colList[0:-2]
X_std = globaldf.filter(colListWithoutCoun)

In [244]:
X_std.head(10)

Name  ENST00000457540.1  ENST00000514057.1  ENST00000379389.4  \
TPM            196.4840           1437.690           367.7920   
TPM             55.4793            944.307           215.8570   
TPM            363.0510            887.574           102.3650   
TPM            191.2670           1220.250           255.4480   
TPM            112.8230           1166.580            94.1861   
TPM            467.3240            958.964           650.9220   
TPM            159.9830           1789.160           149.9470   
TPM             38.0623            748.108           224.2680   
TPM             68.8615            870.636           252.2490   
TPM             76.2010           1133.190           353.5420   

Name  ENST00000321751.9  ENST00000344843.11  ENST00000378609.8  \
TPM          113.679000            105.6110            130.252   
TPM           41.565900            106.5480            121.032   
TPM           68.532500             97.9986            123.957   
TPM           25.567600            103.0060            133.523   
TPM           18.074200            107.8030            147.080   
TPM           29.228000            189.2380            138.050   
TPM           28.587200            131.9820            106.407   
TPM           26.548000            125.6800            117.717   
TPM           57.226800            109.5840            112.708   
TPM            0.000963            131.6900            127.202   

Name  ENST00000234875.8  ENST00000471204.5  ENST00000465387.5  \
TPM             256.294           107.4350           736.9830   
TPM             247.770           418.0080           519.4450   
TPM             364.123            42.9430           992.5330   
TPM             253.019           577.0270            39.8150   
TPM             237.712           369.4070            19.2938   
TPM             270.690           323.3240           476.0180   
TPM             257.988           395.2230            14.8570   
TPM             284.967           646.2090            78.6423   
TPM             279.105           104.9580           872.2870   
TPM             286.373            84.8475           849.8090   

Name  ENST00000493373.5        ...          ENST00000265838.8  \
TPM            130.8080        ...                    58.1557   
TPM            127.0440        ...                    61.3507   
TPM            136.4020        ...                    59.9967   
TPM            129.9660        ...                    53.9273   
TPM             84.9287        ...                    65.0529   
TPM            169.2290        ...                    70.1173   
TPM            102.0910        ...                    51.8823   
TPM            122.0040        ...                    64.9172   
TPM             93.9661        ...                    53.9404   
TPM            134.0640        ...                    52.7156   

Name  ENST00000493643.3  ENST00000445874.1  ENST00000526608.5  \
TPM             41.8480                0.0            8.16222   
TPM             40.2121                0.0            3.33033   
TPM             61.4582                0.0            3.06621   
TPM             38.1569                0.0            2.68920   
TPM             32.0485                0.0            1.13095   
TPM             44.0448                0.0            1.09803   
TPM             36.4706                0.0            4.26536   
TPM             35.7635                0.0            2.35404   
TPM             46.5711                0.0            6.57021   
TPM             43.2223                0.0            8.31847   

Name  ENST00000397511.6  ENST00000528265.1  ENST00000519437.2  \
TPM             41.5422            32.9564            0.00000   
TPM             64.4803            58.3632            0.00000   
TPM             44.3823            54.4039            0.00000   
TPM             63.5692            58.0709            0.00000   
TPM             59.9884            58.0006            0.00000   
TPM             51.

In [368]:
mean_vec = np.mean(X_std, axis=0)
cov_mat = (X_std - mean_vec).T.dot((X_std - mean_vec)) / (X_std.shape[0]-1)
print('Covariance matrix \n%s' %cov_mat)

Covariance matrix 
Name                ENST00000457540.1  ENST00000514057.1  ENST00000379389.4  \
Name                                                                          
ENST00000457540.1        15148.572918       15710.952298       -2614.660497   
ENST00000514057.1        15710.952298      173815.675600      -29724.445120   
ENST00000379389.4        -2614.660497      -29724.445120       48508.084595   
ENST00000321751.9         -160.112808          57.924064         268.988757   
ENST00000344843.11         135.565749        -392.263500        1253.555838   
ENST00000378609.8           -6.354830        -834.413331         294.210922   
ENST00000234875.8         -185.240820         -45.573159       -2174.556549   
ENST00000471204.5         1761.804405       -3545.010209        8232.124212   
ENST00000465387.5        -6428.418825      -20956.902649      -10952.040422   
ENST00000493373.5          565.040978        3354.880771       -1294.636027   
ENST00000338639.9         -887.40

In [369]:
cov_mat.shape

(2569, 2569)

In [370]:
cov_mat = np.cov(X_std.T)

eig_vals, eig_vecs = np.linalg.eig(cov_mat)

print('Eigenvectors \n%s' %eig_vecs)
print('\nEigenvalues \n%s' %eig_vals)

Eigenvectors 
[[  3.74836346e-04 +0.00000000e+00j  -2.76062844e-03 +0.00000000e+00j
    3.31388744e-03 +0.00000000e+00j ...,   4.06673218e-05 +4.42536735e-06j
    4.06673218e-05 -4.42536735e-06j  -1.22132818e-05 +0.00000000e+00j]
 [  4.63784169e-04 +0.00000000e+00j  -2.80169469e-02 +0.00000000e+00j
    2.80720727e-02 +0.00000000e+00j ...,  -2.81433285e-06 -3.43430748e-07j
   -2.81433285e-06 +3.43430748e-07j   8.30739822e-07 +0.00000000e+00j]
 [ -5.60320560e-04 +0.00000000e+00j   7.00171902e-03 +0.00000000e+00j
   -4.43100471e-03 +0.00000000e+00j ...,  -7.93577650e-06 -7.12254224e-07j
   -7.93577650e-06 +7.12254224e-07j  -1.04042645e-06 +0.00000000e+00j]
 ..., 
 [ -1.43791218e-04 +0.00000000e+00j  -8.11285680e-05 +0.00000000e+00j
   -3.27357588e-05 +0.00000000e+00j ...,  -2.15515321e-02 -1.72885412e-02j
   -2.15515321e-02 +1.72885412e-02j  -3.83360086e-02 +0.00000000e+00j]
 [  2.43586603e-05 +0.00000000e+00j  -2.72985489e-04 +0.00000000e+00j
   -4.08017375e-05 +0.00000000e+00j ...,  -3.

In [395]:
eig_vals[2000]

(8.9097811967363756e-13+1.8717384996745579e-13j)

In [375]:
Eig_List = list()
for i in range(len(eig_vals)):
    Eig_List.append(np.abs(eig_vals[i]))

In [396]:
Eig_List[2000]

9.1042630665464104e-13

In [380]:
# Make a list of (eigenvalue, eigenvector) tuples
eig_pairs = [(np.abs(eig_vals[i]), eig_vecs[:,i]) for i in range(len(eig_vals))]

# Sort the (eigenvalue, eigenvector) tuples from high to low
eig_pairs.sort(key=lambda x: x[0], reverse=True)

# Visually confirm that the list is correctly sorted by decreasing eigenvalues
print('Eigenvalues in descending order:')

# for i in eig_pairs:
#     print(i[0])

Eigenvalues in descending order:


In [390]:
eig_pairs[2000][0]

7.9925518402583559e-13

In [433]:
i = 0
indexList = list()
while i < 2000:
    for j in range(len(Eig_List)):
        if eig_pairs[i][0] == Eig_List[j]:
#             print(eig_pairs[i][0],Eig_List[j], j)
            indexList.append(j)
    i += 1

In [434]:
len(indexList)

3529

In [424]:
tot = sum(eig_vals)
var_exp = [(i / tot)*100 for i in sorted(eig_vals, reverse=True)]
cum_var_exp = np.cumsum(var_exp)

In [425]:
colList = globaldf.columns

In [426]:
filterList = list()
for i in range(len(indexList)):
    for j in range(len(colList)):
        if indexList[i] == j:
            filterList.append(colList[j])

In [427]:
maskdf = globaldf.filter(filterList)

In [428]:
maskdf['Country'] = globaldf["Country"].values

In [429]:
maskdf.head(1)

Name  ENST00000457540.1  ENST00000514057.1  ENST00000379389.4  \
TPM             196.484            1437.69            367.792   

Name  ENST00000321751.9  ENST00000344843.11  ENST00000378609.8  \
TPM             113.679             105.611            130.252   

Name  ENST00000234875.8  ENST00000471204.5  ENST00000465387.5  \
TPM             256.294            107.435            736.983   

Name  ENST00000493373.5   ...     ENST00000310786.8  ENST00000435041.2  \
TPM             130.808   ...               99.6481            41.1561   

Name  ENST00000310786.8  ENST00000303436.10  ENST00000243253.7  \
TPM             99.6481             88.4055            65.5821   

Name  ENST00000303436.10  ENST00000243253.7  ENST00000522720.1  \
TPM              88.4055            65.5821                0.0   

Name  ENST00000394920.6  Country  
TPM             11.9341      CEU  

[1 rows x 1582 columns]

In [430]:
maskdf.shape

(369, 1582)

### By doing PCA using Eigen vectors and values the accuracy that we got is around 72.5 %

In [432]:
cross_val = 5
averageAccuracyScore = 0
rf_model = RandomForestClassifier(n_estimators=1500, # Number of trees
                                    max_features=1581,    # Num features considered
                                    oob_score=False)    # Use OOB scoring*
for i in range(cross_val):
    msk = np.random.rand(len(maskdf)) < 0.80

    train = maskdf[msk]
    
    test = maskdf[~msk]


    trainList = maskdf.columns
    trainList = trainList[0:-1]

    features = trainList
    
#     XTrain_std = StandardScaler().fit_transform(train.filter(trainList))
#     XTest_std = StandardScaler().fit_transform(test.filter(trainList))

    # Train the model
    rf_model.fit(X=train[features],
                 y=train["Country"])
    
#     print("OOB accuracy: ")
#     print(rf_model.oob_score_)

    predictedDF = rf_model.predict(test[features])
    ansList = test['Country'].tolist()
    global averageAccuracyScore
    averageAccuracyScore += printAccuracy(ansList,predictedDF)
print("Average Accuracy of model is " + str(averageAccuracyScore/cross_val))

Average Accuracy of model is 0.725286988345812


In [464]:
with open('eqClasses_dict.pickle', 'wb') as handle:
    pickle.dump(eqClasses_dict, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [465]:
with open('eqClasses_dict.pickle', 'rb') as handle:
    eqClasses_dict = pickle.load(handle)

In [ ]:
eqDf = pd.DataFrame.from_dict(eqClasses_dict)

In [ ]:
eqDf = pd.read_csv("eq.csv",low_memory=False)